In [2]:
%pip install pydub


Note: you may need to restart the kernel to use updated packages.


In [1]:
from pydub import AudioSegment
import os

def convert_to_16000_sampling_rate(input_path, output_path):
    sound = AudioSegment.from_file(input_path)
    sound = sound.set_frame_rate(48000)
    sound.export(output_path, format="wav")

def convert_files_to_16000_sampling_rate(file_paths):
    for path in file_paths:
        output_path = os.path.splitext(path)[0]+".wav"
        convert_to_16000_sampling_rate(path, output_path)
        print("Converted:", path, "to", output_path)

# Danh sách đường dẫn đến các tệp âm thanh
file_paths = ['audioDataMFCC/noise/other/exercise_bike.wav',
              'audioDataMFCC/noise/other/pink_noise.wav',
              'audioDataMFCC/noise/_background_noise_/10convert.com_Audience-Claps_daSG5fwdA7o.wav',
              'audioDataMFCC/noise/_background_noise_/running_tap.wav',
              'audioDataMFCC/noise/_background_noise_/doing_the_dishes.wav',
              'audioDataMFCC/noise/_background_noise_/dude_miaowing.wav']

# Chuyển đổi tỷ lệ mẫu của các tệp âm thanh trong danh sách đường dẫn
convert_files_to_16000_sampling_rate(file_paths)


Converted: audioDataMFCC/noise/other/exercise_bike.wav to audioDataMFCC/noise/other/exercise_bike.wav
Converted: audioDataMFCC/noise/other/pink_noise.wav to audioDataMFCC/noise/other/pink_noise.wav
Converted: audioDataMFCC/noise/_background_noise_/10convert.com_Audience-Claps_daSG5fwdA7o.wav to audioDataMFCC/noise/_background_noise_/10convert.com_Audience-Claps_daSG5fwdA7o.wav
Converted: audioDataMFCC/noise/_background_noise_/running_tap.wav to audioDataMFCC/noise/_background_noise_/running_tap.wav
Converted: audioDataMFCC/noise/_background_noise_/doing_the_dishes.wav to audioDataMFCC/noise/_background_noise_/doing_the_dishes.wav
Converted: audioDataMFCC/noise/_background_noise_/dude_miaowing.wav to audioDataMFCC/noise/_background_noise_/dude_miaowing.wav


In [2]:
import os

os.environ["KERAS_BACKEND"] = "tensorflow"

import shutil
import numpy as np

import tensorflow as tf
import keras

from pathlib import Path
from IPython.display import display, Audio

In [3]:
DATASET_ROOT = "audioDataMFCC"

# The folders in which we will put the audio samples and the noise samples
AUDIO_SUBFOLDER = "audio"
NOISE_SUBFOLDER = "noise"

DATASET_AUDIO_PATH = os.path.join(DATASET_ROOT, AUDIO_SUBFOLDER)
DATASET_NOISE_PATH = os.path.join(DATASET_ROOT, NOISE_SUBFOLDER)

# Percentage of samples to use for validation
VALID_SPLIT = 0.15

# Seed to use when shuffling the dataset and the noise
SHUFFLE_SEED = 43

# The sampling rate to use.
# This is the one used in all the audio samples.
# We will resample all the noise to this sampling rate.
# This will also be the output size of the audio wave samples
# (since all samples are of 1 second long)
SAMPLING_RATE = 48000

# The factor to multiply the noise with according to:
#   noisy_sample = sample + noise * prop * scale
#      where prop = sample_amplitude / noise_amplitude
SCALE = 0.5

BATCH_SIZE = 128
EPOCHS = 150
print(DATASET_AUDIO_PATH)

audioDataMFCC\audio


In [4]:
noise_paths = []
for subdir in os.listdir(DATASET_NOISE_PATH):
    subdir_path = Path(DATASET_NOISE_PATH) / subdir
    if os.path.isdir(subdir_path):
        noise_paths += [
            os.path.join(subdir_path, filepath)
            for filepath in os.listdir(subdir_path)
            if filepath.endswith(".wav")
        ]
        print(noise_paths)
if not noise_paths:
    raise RuntimeError(f"Could not find any files at {DATASET_NOISE_PATH}")
print(
    "Found {} files belonging to {} directories".format(
        len(noise_paths), len(os.listdir(DATASET_NOISE_PATH))
    )
)

['audioDataMFCC\\noise\\other\\exercise_bike.wav', 'audioDataMFCC\\noise\\other\\pink_noise.wav']
['audioDataMFCC\\noise\\other\\exercise_bike.wav', 'audioDataMFCC\\noise\\other\\pink_noise.wav', 'audioDataMFCC\\noise\\_background_noise_\\10convert.com_Audience-Claps_daSG5fwdA7o.wav', 'audioDataMFCC\\noise\\_background_noise_\\doing_the_dishes.wav', 'audioDataMFCC\\noise\\_background_noise_\\dude_miaowing.wav', 'audioDataMFCC\\noise\\_background_noise_\\running_tap.wav']
Found 6 files belonging to 2 directories


In [20]:
command = (
    "for dir in `ls -1 " + DATASET_NOISE_PATH + "`; do "
    "for file in `ls -1 " + DATASET_NOISE_PATH + "/$dir/*.wav`; do "
    "sample_rate=`ffprobe -hide_banner -loglevel panic -show_streams "
    "$file | grep sample_rate | cut -f2 -d=`; "
    "if [ $sample_rate -ne 16000 ]; then "
    "ffmpeg -hide_banner -loglevel panic -y "
    "-i $file -ar 16000 temp.wav; "
    "mv temp.wav $file; "
    "fi; done; done"
)
os.system(command)

1

In [5]:
def load_noise_sample(path):
    sample, sampling_rate = tf.audio.decode_wav(
        tf.io.read_file(path), desired_channels=1
    )
    print(sampling_rate," - ", SAMPLING_RATE)
    if sampling_rate == SAMPLING_RATE:
        # Number of slices of 16000 each that can be generated from the noise sample
        slices = int(sample.shape[0] / SAMPLING_RATE)
        sample = tf.split(sample[: slices * SAMPLING_RATE], slices)
        return sample
    else:
        print("Sampling rate for {} is incorrect. Ignoring it".format(path))
        return None
noises = []
print("đây là: ",noise_paths)
for path in noise_paths:
    sample = load_noise_sample(path)
    if sample:
        noises.extend(sample)
noises = tf.stack(noises)

print("Hình dạng của tensor noises:", noises.shape)  # Thêm dòng này để gỡ lỗi


noises = []
for path in noise_paths:
    sample = load_noise_sample(path)
    if sample:
        noises.extend(sample)
noises = tf.stack(noises)

print(
    "{} noise files were split into {} noise samples where each is {} sec. long".format(
        len(noise_paths), noises.shape[0], noises.shape[1] // SAMPLING_RATE
    )
)



đây là:  ['audioDataMFCC\\noise\\other\\exercise_bike.wav', 'audioDataMFCC\\noise\\other\\pink_noise.wav', 'audioDataMFCC\\noise\\_background_noise_\\10convert.com_Audience-Claps_daSG5fwdA7o.wav', 'audioDataMFCC\\noise\\_background_noise_\\doing_the_dishes.wav', 'audioDataMFCC\\noise\\_background_noise_\\dude_miaowing.wav', 'audioDataMFCC\\noise\\_background_noise_\\running_tap.wav']
tf.Tensor(48000, shape=(), dtype=int32)  -  48000
tf.Tensor(48000, shape=(), dtype=int32)  -  48000
tf.Tensor(48000, shape=(), dtype=int32)  -  48000
tf.Tensor(48000, shape=(), dtype=int32)  -  48000
tf.Tensor(48000, shape=(), dtype=int32)  -  48000
tf.Tensor(48000, shape=(), dtype=int32)  -  48000
Hình dạng của tensor noises: (353, 48000, 1)
tf.Tensor(48000, shape=(), dtype=int32)  -  48000
tf.Tensor(48000, shape=(), dtype=int32)  -  48000
tf.Tensor(48000, shape=(), dtype=int32)  -  48000
tf.Tensor(48000, shape=(), dtype=int32)  -  48000
tf.Tensor(48000, shape=(), dtype=int32)  -  48000
tf.Tensor(48000, s

In [11]:
from pydub import AudioSegment

def paths_and_labels_to_dataset(audio_paths, labels):
    """Constructs a dataset of audios and labels."""
    path_ds = tf.data.Dataset.from_tensor_slices(audio_paths)
    
    audio_ds = path_ds.map(
        lambda x: path_to_audio(x), num_parallel_calls=tf.data.AUTOTUNE
    )
    label_ds = tf.data.Dataset.from_tensor_slices(labels)
    return tf.data.Dataset.zip((audio_ds, label_ds))


def path_to_audio(path):
    """Reads and decodes an audio file."""
    audio = tf.io.read_file(path)
    audio, _ = tf.audio.decode_wav(audio, 1, 48000)
    num_samples = tf.shape(audio)[0]
    length_in_seconds = num_samples 
    #tf.print("Đây là Length:", length_in_seconds)

    #print(f"đây là Length: {audio.shape[0]} - [{audio} - {length_in_seconds}")
    #print(path)
    return audio


def add_noise(audio, noises=None, scale=0.5):
    if noises is not None:
        # Create a random tensor of the same size as audio ranging from
        # 0 to the number of noise stream samples that we have.
        tf_rnd = tf.random.uniform(
            (tf.shape(audio)[0],), 0, noises.shape[0], dtype=tf.int32
        )
        noise = tf.gather(noises, tf_rnd, axis=0)

        # Get the amplitude proportion between the audio and the noise
        prop = tf.math.reduce_max(audio, axis=1) / tf.math.reduce_max(noise, axis=1)
        prop = tf.repeat(tf.expand_dims(prop, axis=1), tf.shape(audio)[1], axis=1)

        # Adding the rescaled noise to audio
        audio = audio + noise * prop * scale

    return audio


def audio_to_mfcc(audio, sample_rate, num_mfccs=13):
    # Step 1: STFT
    print(tf.squeeze(audio, axis=-1))
    stfts = tf.signal.stft(tf.squeeze(audio, axis=-1),
                           frame_length=1440,
                           frame_step=480,
                           fft_length=1440,
                           window_fn =tf.signal.hamming_window)
    spectrograms = tf.abs(stfts)
    #print("a: ",spectrograms.shape)

    # Step 2: Warp the linear-scale spectrograms into the mel-scale.
    num_spectrogram_bins = stfts.shape[-1]
    lower_edge_hertz, upper_edge_hertz, num_mel_bins = 80.0, 7600, 40
    linear_to_mel_weight_matrix = tf.signal.linear_to_mel_weight_matrix(
        num_mel_bins, num_spectrogram_bins, 16000, lower_edge_hertz,
        upper_edge_hertz)
    
    #print("b: ",linear_to_mel_weight_matrix.shape[-1:])

    mel_spectrograms = tf.tensordot(
        spectrograms, linear_to_mel_weight_matrix, 1)
    mel_spectrograms.set_shape(spectrograms.shape[:-1].concatenate(
        linear_to_mel_weight_matrix.shape[-1:]))
    
    # Step 3: Compute a stabilized log to get log-magnitude mel-scale spectrograms.
    log_mel_spectrograms = tf.math.log(mel_spectrograms + 1e-6)
    
    # Step 4: Compute MFCCs from log_mel_spectrograms and take the first 13.
    mfccs = tf.signal.mfccs_from_log_mel_spectrograms(
        log_mel_spectrograms)[..., :tf.newaxis]
        
    #print(mfccs)
   
    return mfccs

    

def audio_to_fft(audio):
    # Since tf.signal.fft applies FFT on the innermost dimension,
    # we need to squeeze the dimensions and then expand them again
    # after FFT
    audio = tf.squeeze(audio, axis=-1)
    fft = tf.signal.fft(
        tf.cast(tf.complex(real=audio, imag=tf.zeros_like(audio)), tf.complex64)
    )
    fft = tf.expand_dims(fft, axis=-1)

    # Return the absolute value of the first half of the FFT
    # which represents the positive frequencies
    return tf.math.abs(fft[:, : (audio.shape[1] // 2), :])


# Get the list of audio file paths along with their corresponding labels

class_names = os.listdir(DATASET_AUDIO_PATH)
print(
    "Our class names: {}".format(
        class_names,
    )
)

audio_paths = []
labels = []
for label, name in enumerate(class_names):
    print(
        "Processing speaker {}".format(
            name,
        )
    )
    dir_path = Path(DATASET_AUDIO_PATH) / name
    speaker_sample_paths = [
        os.path.join(dir_path, filepath)
        for filepath in os.listdir(dir_path)
        if filepath.endswith(".wav")
    ]
    audio_paths += speaker_sample_paths
    labels += [label] * len(speaker_sample_paths)

print(
    "Found {} files belonging to {} classes.".format(len(audio_paths), len(class_names))
)

# Shuffle
rng = np.random.RandomState(SHUFFLE_SEED)
rng.shuffle(audio_paths)
rng = np.random.RandomState(SHUFFLE_SEED)
rng.shuffle(labels)

# Split into training and validation
num_val_samples = int(VALID_SPLIT * len(audio_paths))
print("Using {} files for training.".format(len(audio_paths) - num_val_samples))
train_audio_paths = audio_paths[:-num_val_samples]
train_labels = labels[:-num_val_samples]

print("Using {} files for validation.".format(num_val_samples))
valid_audio_paths = audio_paths[-num_val_samples:]
valid_labels = labels[-num_val_samples:]

# Create 2 datasets, one for training and the other for validation
train_ds = paths_and_labels_to_dataset(train_audio_paths, train_labels)
train_ds = train_ds.shuffle(buffer_size=BATCH_SIZE * 8, seed=SHUFFLE_SEED).batch(
    BATCH_SIZE
)

valid_ds = paths_and_labels_to_dataset(valid_audio_paths, valid_labels)
valid_ds = valid_ds.shuffle(buffer_size=32 * 8, seed=SHUFFLE_SEED).batch(32)


# Add noise to the training set
train_ds = train_ds.map(
    lambda x, y: (add_noise(x, noises, scale=SCALE), y),
    num_parallel_calls=tf.data.AUTOTUNE,
)

# Transform audio wave to the frequency domain using `audio_to_fft`
# train_ds = train_ds.map(
#     lambda x, y: (audio_to_fft(x), y), num_parallel_calls=tf.data.AUTOTUNE
# )

# Transform audio wave to the frequency domain using `audio_to_mfcc
train_ds = train_ds.map(
    lambda x, y: (audio_to_mfcc(x, SAMPLING_RATE , num_mfccs=13), y), num_parallel_calls=tf.data.AUTOTUNE
)

train_ds = train_ds.prefetch(tf.data.AUTOTUNE)

# valid_ds = valid_ds.map(
#     lambda x, y: (audio_to_fft(x), y), num_parallel_calls=tf.data.AUTOTUNE
# )
valid_ds = valid_ds.map(
    lambda x, y: (audio_to_mfcc(x, SAMPLING_RATE, num_mfccs=13), y), num_parallel_calls=tf.data.AUTOTUNE
)

valid_ds = valid_ds.prefetch(tf.data.AUTOTUNE)

Our class names: ['Dat', 'Phat', 'Tri', 'Tuan']
Processing speaker Dat
Processing speaker Phat
Processing speaker Tri
Processing speaker Tuan
Found 353 files belonging to 4 classes.
Using 301 files for training.
Using 52 files for validation.
Tensor("Squeeze:0", shape=(None, 48000), dtype=float32)
Tensor("Squeeze:0", shape=(None, 48000), dtype=float32)


In [11]:
for batch in train_ds.take(1):
    features, labels = batch
    print(features.shape)  # Kiểm tra hình dạng của features để đảm bảo không có chiều với kích thước là 0


Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length: 48000
Đây là Length

In [12]:
def residual_block(x, filters, conv_num=3, activation="relu"):
    # Shortcut
    s = keras.layers.Conv2D(filters, (1, 1), padding="same")(x)
    for i in range(conv_num - 1):
        x = keras.layers.Conv2D(filters, (3, 3), padding="same")(x)
        x = keras.layers.Activation(activation)(x)
    x = keras.layers.Conv2D(filters, (3, 3), padding="same")(x)
    x = keras.layers.Add()([x, s])
    x = keras.layers.Activation(activation)(x)
    return x  # Removed max pooling from residual block

def build_model(input_shape, num_classes):
    inputs = keras.layers.Input(shape=input_shape, name="input")

    # Initial Convolutional Layers
    x = keras.layers.Conv2D(32, (3, 3), activation="relu", padding="same")(inputs)
    x = keras.layers.Conv2D(32, (3, 3), activation="relu", padding="same")(x)
    x = keras.layers.MaxPooling2D((2, 2))(x)
    x = keras.layers.BatchNormalization()(x)

    x = keras.layers.Conv2D(64, (3, 3), activation="relu", padding="same")(x)
    x = keras.layers.Conv2D(64, (3, 3), activation="relu", padding="same")(x)
    x = keras.layers.MaxPooling2D((2, 2))(x)
    x = keras.layers.BatchNormalization()(x)

    # Residual Block
    x = residual_block(x, 128)
    x = keras.layers.MaxPooling2D((2, 2))(x)
    x = keras.layers.BatchNormalization()(x)

    # Flatten and Dense Layers
    x = keras.layers.Flatten()(x)
    x = keras.layers.Dense(256, activation="relu", kernel_regularizer=keras.regularizers.l2(0.001))(x)
    x = keras.layers.Dropout(0.5)(x)
    x = keras.layers.Dense(128, activation="relu", kernel_regularizer=keras.regularizers.l2(0.001))(x)
    x = keras.layers.Dropout(0.5)(x)
    
    outputs = keras.layers.Dense(num_classes, activation="softmax")(x)

    # Create model
    model = keras.models.Model(inputs=inputs, outputs=outputs)
    return model



model = build_model((98 , 40, 1), len(class_names))
#model = build_model((SAMPLING_RATE//2 , 1), len(class_names))

model.summary()

# Compile the model using Adam's default learning rate
model.compile(
    optimizer="Adam",
    loss="sparse_categorical_crossentropy",
    metrics=["accuracy"],
)

# Add callbacks:
# 'EarlyStopping' to stop training when the model is not enhancing anymore
# 'ModelCheckPoint' to always keep the model that has the best val_accuracy
model_save_filename = "model.keras"

earlystopping_cb = keras.callbacks.EarlyStopping(patience=10, restore_best_weights=True)
mdlcheckpoint_cb = keras.callbacks.ModelCheckpoint(
    model_save_filename, monitor="val_accuracy", save_best_only=True
)

Model: "functional_3"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input (InputLayer)  │ (None, 98, 40, 1) │          0 │ -                 │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_6 (Conv2D)   │ (None, 98, 40,    │        320 │ input[0][0]       │
│                     │ 32)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_7 (Conv2D)   │ (None, 98, 40,    │      9,248 │ conv2d_6[0][0]    │
│                     │ 32)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ max_pooling2d_3     │ (None, 49, 20,    │          0 │ conv2d_7[0][0]    │
│ (MaxPooling2D)      │ 32)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ batch_normalizatio… │ (None, 49, 20,    │        128 │ max_pooling2d_3[… │
│ (BatchNormalizatio… │ 32)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_8 (Conv2D)   │ (None, 49, 20,    │     18,496 │ batch_normalizat… │
│                     │ 64)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_9 (Conv2D)   │ (None, 49, 20,    │     36,928 │ conv2d_8[0][0]    │
│                     │ 64)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ max_pooling2d_4     │ (None, 24, 10,    │          0 │ conv2d_9[0][0]    │
│ (MaxPooling2D)      │ 64)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ batch_normalizatio… │ (None, 24, 10,    │        256 │ max_pooling2d_4[… │
│ (BatchNormalizatio… │ 64)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_11 (Conv2D)  │ (None, 24, 10,    │     73,856 │ batch_normalizat… │
│                     │ 128)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ activation          │ (None, 24, 10,    │          0 │ conv2d_11[0][0]   │
│ (Activation)        │ 128)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_12 (Conv2D)  │ (None, 24, 10,    │    147,584 │ activation[0][0]  │
│                     │ 128)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ activation_1        │ (None, 24, 10,    │          0 │ conv2d_12[0][0]   │
│ (Activation)        │ 128)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_13 (Conv2D)  │ (None, 24, 10,    │    147,584 │ activation_1[0][… │
│                     │ 128)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_10 (Conv2D)  │ (None, 24, 10,    │      8,320 │ batch_normalizat… │
│                     │ 128)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ add (Add)           │ (None, 24, 10,    │          0 │ conv2d_13[0][0],  │
│                     │ 128)              │            │ conv2d_10[0][0]   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ activation_2        │ (None, 24, 10,    │          0 │ add[0][0]         │
│ (Activation)        │ 128)              │            │                 

 Total params: 2,442,980 (9.32 MB)

 Trainable params: 2,442,532 (9.32 MB)

 Non-trainable params: 448 (1.75 KB)

In [13]:
history = model.fit(
    train_ds,
    epochs=EPOCHS,
    validation_data=valid_ds,
    callbacks=[ mdlcheckpoint_cb],
)

Epoch 1/150
3/3 ━━━━━━━━━━━━━━━━━━━━ 16s 2s/step - accuracy: 0.2742 - loss: 4.1292 - val_accuracy: 0.4038 - val_loss: 2.0371
Epoch 2/150
3/3 ━━━━━━━━━━━━━━━━━━━━ 5s 1s/step - accuracy: 0.2874 - loss: 2.9940 - val_accuracy: 0.2115 - val_loss: 2.0565
Epoch 3/150
3/3 ━━━━━━━━━━━━━━━━━━━━ 5s 1s/step - accuracy: 0.4014 - loss: 2.3247 - val_accuracy: 0.2308 - val_loss: 2.0742
Epoch 4/150
3/3 ━━━━━━━━━━━━━━━━━━━━ 5s 1s/step - accuracy: 0.4538 - loss: 2.1531 - val_accuracy: 0.1538 - val_loss: 2.0559
Epoch 5/150
3/3 ━━━━━━━━━━━━━━━━━━━━ 5s 1s/step - accuracy: 0.4953 - loss: 1.9881 - val_accuracy: 0.2692 - val_loss: 2.0756
Epoch 6/150
3/3 ━━━━━━━━━━━━━━━━━━━━ 5s 1s/step - accuracy: 0.5132 - loss: 1.9601 - val_accuracy: 0.2692 - val_loss: 2.0976
Epoch 7/150
3/3 ━━━━━━━━━━━━━━━━━━━━ 5s 1s/step - accuracy: 0.5307 - loss: 1.9383 - val_accuracy: 0.3846 - val_loss: 2.0982
Epoch 8/150
3/3 ━━━━━━━━━━━━━━━━━━━━ 9s 3s/step - accuracy: 0.5975 - loss: 1.7292 - val_accuracy: 0.4231 - val_loss: 2.0439
Epoch 9

In [14]:
print(model.evaluate(valid_ds))


2/2 ━━━━━━━━━━━━━━━━━━━━ 1s 92ms/step - accuracy: 0.9151 - loss: 0.6480
[0.7382112741470337, 0.9038461446762085]


In [15]:
model.save('MFCC-40bin-hamming-newmodel.h5')


In [16]:
keras.saving.save_model(model,'MFCC-40bin-hamming-newmodel.keras')

In [54]:
SAMPLES_TO_DISPLAY = 50

test_ds = paths_and_labels_to_dataset(valid_audio_paths, valid_labels)
test_ds = test_ds.shuffle(buffer_size=BATCH_SIZE * 8, seed=SHUFFLE_SEED).batch(
    BATCH_SIZE
)

test_ds = test_ds.map(
    lambda x, y: (add_noise(x, noises, scale=SCALE), y),
    num_parallel_calls=tf.data.AUTOTUNE,
)

for audios, labels in test_ds.take(1):
    # Get the signal FFT
    ffts = audio_to_mfcc(audios,1,48000)
    # Predict
    y_pred = model.predict(ffts)
    # Take random samples
    rnd = np.random.randint(0, audios.shape[0], SAMPLES_TO_DISPLAY)
    audios = audios.numpy()[rnd, :, :]
    labels = labels.numpy()[rnd]
    y_pred = np.argmax(y_pred, axis=-1)[rnd]

    for index in range(SAMPLES_TO_DISPLAY):
        # For every sample, print the true and predicted label
        # as well as run the voice with the noise
        print(
            "Speaker:\33{} {}\33[0m\tPredicted:\33{} {}\33[0m".format(
                "[92m" if labels[index] == y_pred[index] else "[91m",
                class_names[labels[index]],
                "[92m" if labels[index] == y_pred[index] else "[91m",
                class_names[y_pred[index]],
            )
        )
        display(Audio(audios[index, :, :].squeeze(), rate=16000))

tf.Tensor(
[[-0.00460815 -0.00622559 -0.00695801 ... -0.01730347 -0.01651001
   0.00823975]
 [ 0.00865566  0.00092232 -0.00681101 ...  0.02475986 -0.01005713
  -0.0455455 ]
 [ 0.00787114  0.00857287  0.0092441  ... -0.00408496 -0.0042399
  -0.00442536]
 ...
 [-0.0348211  -0.03713724 -0.03945338 ...  0.02231839  0.00672208
  -0.00628023]
 [ 0.09036968  0.06664006  0.04293571 ...  0.05257309  0.03326511
   0.01313316]
 [ 0.09505901  0.10852194  0.11102907 ... -0.06889586 -0.07322935
  -0.07597592]], shape=(52, 48000), dtype=float32)
a:  (52, 98, 721)
b:  (40,)
tf.Tensor(
[[[ 2.02761478e+01  2.67695713e+00 -9.03419971e-01 ... -1.51708731e-02
   -6.90793339e-03  2.31590211e-01]
  [ 2.38967133e+01  2.96614194e+00 -1.34717298e+00 ...  1.85519874e-01
    3.35318804e-01  1.59420490e-01]
  [ 2.37487907e+01  3.14279270e+00 -1.08196497e+00 ... -6.63173720e-02
    4.61788550e-02  7.32702091e-02]
  ...
  [ 2.14773216e+01  2.51085854e+00 -1.78011906e+00 ... -1.30904183e-01
   -1.90553010e-01 -1.1226

Speaker: Tuan	Predicted: Tuan


Speaker: Tuan	Predicted: Tuan


Speaker: Tuan	Predicted: Tuan


Speaker: Tri	Predicted: Tri


...

Speaker: Tri	Predicted: Tri


Speaker: Dat	Predicted: Dat


Speaker: Tri	Predicted: Tri


Speaker: Phat	Predicted: Phat


Speaker: Tri	Predicted: Tri


In [18]:
import sounddevice as sd
import numpy as np
import librosa
from tensorflow.keras.models import load_model
import tensorflow as tf
import soundfile as sf
import os


def record_audio(path):

    audio = tf.io.read_file(path)
    # Decode the audio bytes
    audio_tensor, _ = tf.audio.decode_wav(audio, 1, 48000)
    num_samples = tf.shape(audio_tensor)[0]
    length_in_seconds = num_samples 
    print("num_samples: ",num_samples)
    return audio_tensor.numpy().flatten()

def predict_audio(audio, model, class_names):
    # Preprocess the audio
    audio = np.expand_dims(audio, axis=0)  # Add batch dimension
    audio = np.expand_dims(audio, axis=-1)  # Add channel dimension
    mfccs = audio_to_mfcc(audio, SAMPLING_RATE, num_mfccs=13)
    
    # Make predictions
    predictions = model.predict(mfccs)
    print("đây là:",predictions[0])
    # Get the predicted class
    predicted_class_index = np.argmax(predictions[0])
    predicted_class = class_names[predicted_class_index]
    
    return predicted_class

# Load the model
model = load_model('MFCC-40bin-hamming-newmodel.keras')
folder_path = "TestAudio"
# Ghi âm trong 3 giây và dự đoán
for file_name in os.listdir(folder_path):
    if file_name.endswith(".wav"):
        file_path = os.path.join(folder_path, file_name)
        #print("Processing file:", file_name)
        
        # Ghi âm từ tệp và dự đoán
        recorded_audio = record_audio(file_path)
        predicted_class = predict_audio(recorded_audio, model, class_names)
        print(f"file of {file_name} - Predict:", predicted_class)

c:\Users\Phat\anaconda3\Lib\site-packages\keras\src\saving\saving_lib.py:396: UserWarning: Skipping variable loading for optimizer 'rmsprop', because it has 30 variables whereas the saved optimizer has 58 variables. 
  trackable.load_own_variables(weights_store.get(inner_path))


num_samples:  tf.Tensor(48000, shape=(), dtype=int32)
tf.Tensor([[0.         0.         0.         ... 0.26229858 0.33773804 0.26031494]], shape=(1, 48000), dtype=float32)
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 1s/step
đây là: [2.1893916e-08 9.9999726e-01 2.8078390e-10 2.7491808e-06]
file of dat_1.wav - Predict: Phat
num_samples:  tf.Tensor(48000, shape=(), dtype=int32)
tf.Tensor(
[[ 0.12271118  0.20846558  0.29156494 ...  0.03823853  0.01852417
  -0.00061035]], shape=(1, 48000), dtype=float32)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 60ms/step
đây là: [1.00000000e+00 2.32853403e-09 5.69607209e-11 1.43898435e-11]
file of dat_2.wav - Predict: Dat
num_samples:  tf.Tensor(48000, shape=(), dtype=int32)
tf.Tensor(
[[-0.01010132  0.00161743  0.04922485 ... -0.02719116 -0.0324707
  -0.04101562]], shape=(1, 48000), dtype=float32)
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 53ms/step
đây là: [1.5216740e-06 9.9986172e-01 2.5506257e-05 1.1122872e-04]
file of dat_3.wav - Predict: Phat
num_samples:  tf.Tensor(48000, shape=(), dtype=int32